# AutoGen Agents w Produkcji: Obserwowalność i Ocena

W tym poradniku nauczymy się, jak **monitorować wewnętrzne kroki (śledzenie) [agentów Autogen](https://github.com/microsoft/autogen)** oraz **oceniać ich wydajność** za pomocą [Langfuse](https://langfuse.com).

Ten przewodnik obejmuje **online** i **offline** metryki oceny, które zespoły wykorzystują, aby szybko i niezawodnie wprowadzać agentów do produkcji.

**Dlaczego ocena agentów AI jest ważna:**
- Rozwiązywanie problemów, gdy zadania zawodzą lub dają nieoptymalne wyniki
- Monitorowanie kosztów i wydajności w czasie rzeczywistym
- Poprawa niezawodności i bezpieczeństwa dzięki ciągłemu feedbackowi


## Krok 1: Ustaw zmienne środowiskowe

Zdobądź swoje klucze API Langfuse, rejestrując się w [Langfuse Cloud](https://cloud.langfuse.com/) lub [hostując Langfuse samodzielnie](https://langfuse.com/self-hosting).

_**Uwaga:** Osoby hostujące samodzielnie mogą użyć [modułów Terraform](https://langfuse.com/self-hosting/azure), aby wdrożyć Langfuse na platformie Azure. Alternatywnie, możesz wdrożyć Langfuse na Kubernetesie, korzystając z [Helm chart](https://langfuse.com/self-hosting/kubernetes-helm)._


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

Po ustawieniu zmiennych środowiskowych możemy teraz zainicjalizować klienta Langfuse. `get_client()` inicjalizuje klienta Langfuse przy użyciu poświadczeń podanych w zmiennych środowiskowych.


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## Krok 2: Inicjalizacja instrumentacji OpenLit

Teraz inicjalizujemy instrumentację [OpenLit](https://github.com/openlit/openlit). OpenLit automatycznie rejestruje operacje AutoGen i eksportuje zakresy OpenTelemetry (OTel) do Langfuse.


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## Krok 3: Uruchom swojego agenta

Teraz konfigurujemy agenta wieloetapowego, aby przetestować nasze instrumentarium.


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### Struktura śladu

Langfuse zapisuje **ślad**, który zawiera **spany**, reprezentujące każdy krok logiki Twojego agenta. W tym przypadku ślad obejmuje ogólny przebieg działania agenta oraz podspany dla:
- Agenta planującego posiłki
- Agentów dietetycznych

Możesz je przeanalizować, aby dokładnie zobaczyć, gdzie jest poświęcany czas, ile tokenów jest używanych i tak dalej:

![Drzewo śladu w Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[Link do śladu](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## Ocena Online

Ocena Online odnosi się do oceny agenta w rzeczywistym, działającym środowisku, czyli podczas faktycznego użytkowania w produkcji. Polega to na monitorowaniu wydajności agenta w interakcjach z prawdziwymi użytkownikami oraz na ciągłej analizie wyników.

### Typowe metryki do śledzenia w produkcji

1. **Koszty** — Instrumentacja rejestruje użycie tokenów, które można przekształcić w przybliżone koszty, przypisując cenę za token.
2. **Opóźnienie** — Obserwuj czas potrzebny na wykonanie każdego kroku lub całego procesu.
3. **Opinie użytkowników** — Użytkownicy mogą przekazywać bezpośrednie opinie (np. kciuk w górę/w dół), co pomaga w ulepszaniu lub korygowaniu działania agenta.
4. **LLM jako sędzia** — Wykorzystaj oddzielny LLM do oceny wyników agenta w niemal rzeczywistym czasie (np. sprawdzając toksyczność lub poprawność).

Poniżej przedstawiamy przykłady tych metryk.


#### 1. Koszty

Poniżej znajduje się zrzut ekranu przedstawiający użycie wywołań `gpt-4o-mini`. Jest to przydatne do identyfikacji kosztownych kroków i optymalizacji działania agenta.

![Koszty](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[Link do śladu](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. Opóźnienie

Możemy również sprawdzić, ile czasu zajęło wykonanie każdego kroku. W poniższym przykładzie cała operacja trwała około 3 sekundy, co można rozbić na poszczególne etapy. To pozwala zidentyfikować wąskie gardła i zoptymalizować działanie agenta.

![Opóźnienie](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[Link do śladu](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. Opinie użytkowników

Jeśli Twój agent jest zintegrowany z interfejsem użytkownika, możesz rejestrować bezpośrednie opinie użytkowników (na przykład kciuk w górę/w dół w interfejsie czatu).


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

Opinie użytkowników są następnie rejestrowane w Langfuse:

![Opinie użytkowników są rejestrowane w Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. Automatyczne ocenianie za pomocą LLM-as-a-Judge

LLM-as-a-Judge to kolejny sposób na automatyczną ocenę wyników działania Twojego agenta. Możesz skonfigurować osobne wywołanie LLM, aby ocenić poprawność, toksyczność, styl lub inne kryteria, które są dla Ciebie istotne.

**Przebieg**:
1. Definiujesz **Szablon Oceny**, np. "Sprawdź, czy tekst jest toksyczny."
2. Ustawiasz model, który będzie pełnił rolę sędziego; w tym przypadku `gpt-4o-mini` wywoływany za pomocą Azure.
3. Za każdym razem, gdy Twój agent generuje wynik, przekazujesz ten wynik do "sędziego" LLM wraz z szablonem.
4. LLM pełniący rolę sędziego odpowiada oceną lub etykietą, którą zapisujesz w narzędziu do monitorowania.

Przykład z Langfuse:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

Możesz zauważyć, że odpowiedź w tym przykładzie została oceniona jako „nie toksyczna”.

![Ocena odpowiedzi przez LLM jako sędziego](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. Przegląd metryk obserwowalności

Wszystkie te metryki można wizualizować razem na pulpitach nawigacyjnych. Dzięki temu możesz szybko zobaczyć, jak Twój agent działa w wielu sesjach, oraz śledzić metryki jakości w czasie.

![Przegląd metryk obserwowalności](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## Ocena offline

Ocena online jest kluczowa dla bieżącej informacji zwrotnej, ale równie ważna jest **ocena offline**—systematyczne sprawdzanie przed lub w trakcie procesu tworzenia. Pomaga to utrzymać jakość i niezawodność przed wprowadzeniem zmian do produkcji.


### Ocena Zbioru Danych

Podczas oceny offline zazwyczaj:
1. Masz zestaw danych referencyjnych (zawierający pary: pytanie i oczekiwana odpowiedź)
2. Uruchamiasz swojego agenta na tym zbiorze danych
3. Porównujesz wyniki z oczekiwanymi rezultatami lub korzystasz z dodatkowego mechanizmu oceny

Poniżej przedstawiamy to podejście na przykładzie [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset), który zawiera pytania i oczekiwane odpowiedzi.


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

Następnie tworzymy jednostkę zbioru danych w Langfuse, aby śledzić uruchomienia. Następnie dodajemy każdy element ze zbioru danych do systemu.


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![Elementy zbioru danych w Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### Uruchamianie agenta na zbiorze danych

Najpierw tworzymy prostego agenta Autogen, który odpowiada na pytania, korzystając z modeli Azure OpenAI.


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

Następnie definiujemy funkcję pomocniczą `my_agent()`.


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

Na koniec przechodzimy przez każdy element zestawu danych, uruchamiamy agenta i łączymy ślad z elementem zestawu danych. Możemy również dołączyć szybki wynik oceny, jeśli jest to pożądane.


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

Możesz powtórzyć ten proces z różnymi konfiguracjami agentów, takimi jak:
- Modele (gpt-4o-mini, gpt-4.1, itd.)
- Prompty
- Narzędzia (wyszukiwanie vs. brak wyszukiwania)
- Złożoność agenta (wielu agentów vs. pojedynczy agent)

Następnie porównaj je obok siebie w Langfuse. W tym przykładzie uruchomiłem agenta 3 razy na 25 pytaniach z zestawu danych. Przy każdym uruchomieniu użyłem innego modelu Azure OpenAI. Możesz zauważyć, że liczba poprawnie udzielonych odpowiedzi wzrasta przy użyciu większego modelu (zgodnie z oczekiwaniami). Wynik `correct_answer` jest tworzony przez [Evaluator LLM-as-a-Judge](https://langfuse.com/docs/scores/model-based-evals), który został skonfigurowany do oceny poprawności pytania na podstawie przykładowej odpowiedzi podanej w zestawie danych.

![Przegląd uruchomienia zestawu danych](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![Porównanie uruchomienia zestawu danych](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)



---

**Zastrzeżenie**:  
Ten dokument został przetłumaczony za pomocą usługi tłumaczenia AI [Co-op Translator](https://github.com/Azure/co-op-translator). Chociaż dokładamy wszelkich starań, aby tłumaczenie było precyzyjne, prosimy pamiętać, że automatyczne tłumaczenia mogą zawierać błędy lub nieścisłości. Oryginalny dokument w jego rodzimym języku powinien być uznawany za źródło autorytatywne. W przypadku informacji o kluczowym znaczeniu zaleca się skorzystanie z profesjonalnego tłumaczenia wykonanego przez człowieka. Nie ponosimy odpowiedzialności za jakiekolwiek nieporozumienia lub błędne interpretacje wynikające z użycia tego tłumaczenia.
